In [1]:
import math
import string
import numpy as np

In [5]:
# signes est une chaîne de caractère contenant tous les signes utilisés dans les messages
# on ajoute l'alphabet majuscule et majuscule grâce à string.ascii_uppercase+string.ascii_lowercase
# la commande list transforme une chaîne de caractère en liste

L=list(' '+string.ascii_uppercase+string.ascii_lowercase+'.?!,0123456789') 
print(L)

[' ', 'A', 'B', 'C', 'D', 'E', 'F', 'G', 'H', 'I', 'J', 'K', 'L', 'M', 'N', 'O', 'P', 'Q', 'R', 'S', 'T', 'U', 'V', 'W', 'X', 'Y', 'Z', 'a', 'b', 'c', 'd', 'e', 'f', 'g', 'h', 'i', 'j', 'k', 'l', 'm', 'n', 'o', 'p', 'q', 'r', 's', 't', 'u', 'v', 'w', 'x', 'y', 'z', '.', '?', '!', ',', '0', '1', '2', '3', '4', '5', '6', '7', '8', '9']


In [8]:
nL = len(L) # nombre de caractères dans notre langage
print(nL)

67


In [9]:
def codage(M):
    n = 0
    for k in range(len(M)):
        n = n + L.index(M[k])*nL**k
    return n
        

In [10]:
M = "Hello world!"
codage(M)

6772894412117139825371

In [11]:
def Base(n,b): #Ecriture de n en base b (cf TP précédent), on s'en servira plus tard
    L=[]
    while n>0:
        L=L+[n%b]
        n=n//b
    return L  
    

In [12]:
def BaseNb(l,b): # renvoie le nombre à partir de la liste de son écriture en base b
    n = 0
    for k in range(len(l)):
        n = n + l[k]*b**k
    return n
 

In [13]:
# On renvoie un couple d, [u,v] où d=pgcd(a,b) et ua+bv = d, cf TP algo d'Euclide

def Euclide(a,b):
    X=np.array([[a],[b]])          # vecteur colonne (a,b)
    P=np.array([[1,0],[0,1]])      # Matrice identité
    if a<b:  
        X=np.array([[b],[a]])      # Si a et plus petit que b on les inverse
        P=np.array([[0,1],[1,0]])  # Matrice pour inverser a et b par laquel il faudra multiplier
    while X[1,0]!=0:               # On boucle tant qu'on n'a pas atteint le vecteur (d,0) (qui signifie la fin de l'algo)
        Q=np.array([[0, 1], [1,-(X[0,0]//X[1,0])]])
        X= Q@X                     # On remplace le vecteur (a,b) par (b,a-bq) où q est le quotient de a par b
        P = Q@P                    # On garde en mémoire le produit matriciel pour pouvoir avoir les coeff de Bézout à la fin 
    return X[0,0], P[0,:]   


In [14]:
def decodage(n):
    M = ""
    G = Base(n,nL) # tableau donnant l'écriture de n en base nL (cf au début pour la déf)
    for k in G:
        M = M+L[k]
    return M

In [19]:
M = "Hello world"
k = codage(M)
print(k)
print(decodage(k))

55737102343898885806
Hello world


In [20]:
def Coder(M,N):
    return Base(codage(M),N)

In [21]:
def Decoder(l,N):
    return decodage(BaseNb(l,N))

In [25]:
M = "Hello world!"
G = Coder(M,691)
print(G)

print(Decoder(G,691))

[335, 395, 541, 274, 361, 389, 26, 90]
Hello world!


In [30]:
# e et n sont supposés premiers entre eux. On pourrait ajouter un test pour le vérifier.
# On renvoie d entre 0 et n-1 tel que e*d = 1 mod n
def Inverse(e,n): 
    (u,v) = Euclide(e,n)[1] # on récupère les coeff de Bézout de sorte que ue + nv = pgcd(e,n)
    return u%n # en prenant u mod n on obtient un nombre entre 0 et n-1

In [32]:
# On teste avec e = 37 et n = 11. On trouve d = 3. On vérifie que 3*37 = 1 mod 11
d=Inverse(37,11)
print(d)
print(d*37%11)


3
1


In [36]:
def ExpRapide(a,n,N): #Calcul de a^n modulo N par exponentiation rapide, cf TP Précédent
    L=Base(n,2)
    P=[a%N]
    for i in range(len(L)):  #Calcul des carrés itérés de a modulo N
        b=(P[i]*P[i])%N
        P=P+[b]
    p=1
    for i in range(len(L)): #Calcul le produit des carrés itérés de a associés aux coefficients non nuls de L
        if L[i]!=0:
            p=(p*P[i])%N
    return p

In [37]:
# l = liste d'entiers. On élève chacun des éléments de l à la puissance k et on réduit mod N
# Il est important d'utiliser l'exponentiation rapide sinon les temps de calculs sont trop longs
def Puissance(l,k,N):
    G = []
    for i in l:
        G = G+[ExpRapide(i,k,N)]
    return G

In [38]:
Puissance([1,2,3,4,5],10,37)

[1, 25, 34, 33, 30]

In [123]:
# On vérifie sur le dernier élément que 37 à  la puissance 10 est congru à 30 mod 37...
5**10%37

30

In [124]:
# M =  message à chiffrer, e = partie de la clef publique

def Chiffrer(M,N,e):
    l = Coder(M,N) # On transforme le message M en un tableau de nombre entre 0 et N-1
    return Puissance(l,e,N) # On code le message en élevant à la puissance e

In [39]:
#  l = message chiffré à décoder. d = clef privée
def Dechiffrer(l,N,d):
    L = Puissance(l,d,N) # on décode en élevant à la puissance d
    return Decoder(L,N)  # on transforme le tableau d'entiers en message

In [40]:
p = 440334654777631
q = 145295143558111
N = p*q

In [41]:
# On teste si un nombre est premier
def isPrime(n):
    for i in range(2,int(n**0.5)+1):
        if n%i==0:
            return False       
    return True

In [42]:
print(isPrime(p))
print(isPrime(q))

True
True


True

In [131]:
e = 1193

In [133]:
d = Inverse(e,(p-1)*(q-1))
print(d)

30568095156186201333234581057


In [132]:
np.gcd(e,(p-1)*(q-1))

1

In [144]:
M = "Hello world! Quelle est la longueur du cercle ? En supposant son rayon qui vaut 1... et sans utiliser apostrophes et accents"

In [146]:
H = Chiffrer(M,N,e)

In [147]:
Dechiffrer(H,N,d)

'Hello world! Quelle est la longueur du cercle ? En supposant son rayon qui vaut 1... et sans utiliser apostrophes et accents'

In [39]:
codage(M)

12208690884647187408